# 🏠 Necesidad de vivienda

## 📊 Población

In [1]:
# --- Librerías únicas y ordenadas ---
import sys
import numpy as np
import pandas as pd
from pathlib import Path

sys.path.append('../Funciones')
from Funciones_v2 import  leer_archivo, diagnostico_base_datos_pdf, limpiar_base_vivienda

# Carga global del archivo para evitar lecturas repetidas en cada llamada a la función
CLAVES_PATH = Path("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Bases de datos/Claves_Estado_Municipio.xlsx")
DF_CLAVES = leer_archivo(CLAVES_PATH)

def obtener_claves_estado_mun(nombre_entidad, nombre_municipio=None, retornar_resultado=False):

    """
    Devuelve claves de entidad y municipio si se solicita explícitamente.
    En caso de error o error tipográfico, sugiere o informa el problema.

    Parámetros:
    ------------
    nombre_entidad : str
        Nombre del estado (ej. "Sinaloa").
    nombre_municipio : str, opcional
        Nombre del municipio (ej. "Mazatlán").
    retornar_resultado : bool
        Si es True, retorna un dict con claves correctas. Si es False, solo reporta errores/sugerencias.

    Retorna:
    --------
    None si todo está correcto y retornar_resultado=False.
    Mensaje de error o sugerencia si hay problemas.
    Claves {'CVE_ENT': ..., 'CVE_MUN': ...} si retornar_resultado=True.
    """
    nombre_entidad = nombre_entidad.strip().title()
    nombre_municipio = nombre_municipio.strip().title() if nombre_municipio else None

    entidades = DF_CLAVES['NOM_ENT'].unique()

    if nombre_entidad not in entidades:
        sugerencias = get_close_matches(nombre_entidad, entidades, n=1, cutoff=0.6)
        return f"¿Quisiste decir '{sugerencias[0]}'?" if sugerencias else f"'{nombre_entidad}' no es válido."

    df_ent = DF_CLAVES[DF_CLAVES['NOM_ENT'] == nombre_entidad]

    if not nombre_municipio:
        return {'CVE_ENT': df_ent['CVE_ENT'].iloc[0]} if retornar_resultado else None

    municipios = df_ent['NOM_MUN'].unique()

    if nombre_municipio not in municipios:
        sugerencias = get_close_matches(nombre_municipio, municipios, n=1, cutoff=0.6)
        if sugerencias:
            return f"¿Quisiste decir '{sugerencias[0]}'?"
        mun_otro = DF_CLAVES[DF_CLAVES['NOM_MUN'] == nombre_municipio]
        if not mun_otro.empty:
            estados = mun_otro['NOM_ENT'].unique()
            return f"'{nombre_municipio}' pertenece a: {', '.join(estados)}"
        return f"'{nombre_municipio}' no se encontró en ningún estado."

    fila = df_ent[df_ent['NOM_MUN'] == nombre_municipio].iloc[0]
    return {'CVE_ENT': fila['CVE_ENT'], 'CVE_MUN': fila['CVE_MUN']} if retornar_resultado else None

def corregir_nombres_estado_municipio(estado, municipio):
    """
    Normaliza nombres de estado y municipio usando las claves oficiales.

    Parámetros:
    ------------
    estado : str
    municipio : str

    Retorna:
    --------
    estado_normalizado, municipio_normalizado : tuple[str, str]
        Los nombres corregidos y en formato oficial según DF_CLAVES.
    
    Lanza:
    ------
    ValueError si hay errores ortográficos que no pueden corregirse.
    """
    estado = estado.strip().title()
    municipio = municipio.strip().title()

    entidades = DF_CLAVES['NOM_ENT'].unique()
    if estado not in entidades:
        sugerencia = get_close_matches(estado, entidades, n=1, cutoff=0.6)
        raise ValueError(f"Estado no encontrado. ¿Quisiste decir '{sugerencia[0]}'?" if sugerencia else f"'{estado}' no es un estado válido.")

    df_ent = DF_CLAVES[DF_CLAVES['NOM_ENT'] == estado]
    municipios = df_ent['NOM_MUN'].unique()
    if municipio not in municipios:
        sugerencia = get_close_matches(municipio, municipios, n=1, cutoff=0.6)
        raise ValueError(f"Municipio no encontrado. ¿Quisiste decir '{sugerencia[0]}'?" if sugerencia else f"'{municipio}' no está en el estado '{estado}'.")

    # Recuperar nombres corregidos (como aparecen en el archivo oficial)
    estado_corregido = df_ent['NOM_ENT'].iloc[0]
    municipio_corregido = df_ent[df_ent['NOM_MUN'] == municipio]['NOM_MUN'].iloc[0]
    return estado_corregido, municipio_corregido



In [2]:
# Seleccionar el estado y municipio para el modelo
estado = "Sinaloa"
municipio = "mazatlán"

# Obtener 'CVE_ENT' y 'CVE_MUN' 
claves= obtener_claves_estado_mun(estado,municipio,retornar_resultado=True)

# Corregir nombres de estado y municipio
estado, municipio = corregir_nombres_estado_municipio(estado, municipio)

# Imprimir siempre el estado
print(f"Estado: {claves['CVE_ENT']}")

# Solo imprimir municipio si existe
if 'CVE_MUN' in claves:
    print(f"Municipio: {claves['CVE_MUN']}")

Estado: 25
Municipio: 12


In [3]:
# Importar la base de datos de la población 2020 por AGEB
ruta_2020= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Proyecto Villa Union/Base de datos/Sinaloa_2020.csv"
df_2020 = leer_archivo(ruta_2020)
#diagnostico_base_datos_pdf(df_2020, nombre_pdf="diagnostico_datos.pdf")
df_2020 = limpiar_base_vivienda(df_2020)
df_2020

🔍 Limpieza completa:
 - Columnas eliminadas: 2
 - Columnas restantes: 284
 - Filas totales: 5552


MUN                      NOM_MUN   LOC                       NOM_LOC  \
0       0  Total de la entidad Sinaloa     0           Total de la Entidad   
1       0  Total de la entidad Sinaloa  9998   Localidades de una vivienda   
2       0  Total de la entidad Sinaloa  9999  Localidades de dos viviendas   
3       1                        Ahome     0           Total del Municipio   
4       1                        Ahome     1                    Los Mochis   
...   ...                          ...   ...                           ...   
5547   18                     Navolato  2305        Rancho los 4 Potrillos   
5548   18                     Navolato  2308                    El Tapacal   
5549   18                     Navolato  2311         Campo Paredes Gaxiola   
5550   18                     Navolato  9998   Localidades de una vivienda   
5551   18                     Navolato  9999  Localidades de dos viviendas   

              LONGITUD          LATITUD ALTITUD   POBTOT   POBFEM   POBMAS  \
0                  NaN              NaN     NaN  3026943  1532128  1494815   
1                  NaN              NaN     NaN    20358     8853    11505   
2                  NaN              NaN     NaN     6701     2062     4639   
3                  NaN              NaN     NaN   459310   233994   225316   
4     108°59'39.634" W  25°47'00.301" N    0009   298009   154344   143665   
...                ...              ...     ...      ...      ...      ...   
5547  107°53'00.488" W  24°39'59.832" N    0005        4      NaN      NaN   
5548  107°32'34.902" W  24°38'42.425" N    0008        3      NaN      NaN   
5549  107°46'46.899" W  24°46'13.940" N    0009      229      NaN      NaN   
5550               NaN              NaN     NaN     4207     1835     2372   
5551               NaN              NaN     NaN      509      227      282   

      ... VPH_CEL VPH_INTER VPH_STVP VPH_SPMVPI VPH_CVJ VPH_SINRTV VPH_SINLTC  \
0     ...  787350    441062   457908     162367   92477      35425      50477   
1     ...    1661       215      784         41      29        283        288   
2     ...     724        80      370         13      13        209        236   
3     ...  125204     73174    63943      24619   12881       4521       6866   
4     ...   87110     61100    45292      22380   11601       2119       2540   
...   ...     ...       ...      ...        ...     ...        ...        ...   
5547  ...     NaN       NaN      NaN        NaN     NaN        NaN        NaN   
5548  ...     NaN       NaN      NaN        NaN     NaN        NaN        NaN   
5549  ...     NaN       NaN      NaN        NaN     NaN        NaN        NaN   
5550  ...     112        18       42          2       2          7          8   
5551  ...      46         7       12          0       1          5          7   

     VPH_SINCINT VPH_SINTIC TAMLOC  
0         365642      12648    NaN  
1           1662        140    NaN  
2            857        129    NaN  
3          53318       1470    NaN  
4          24902        409     12  
...          ...        ...    ...  
5547         NaN        NaN      1  
5548         NaN        NaN      1  
5549         NaN        NaN      1  
5550          94          3    NaN  
5551          44          2    NaN  

[5552 rows x 284 columns]